In [1]:
import os
import pandas as pd
import xml.etree.ElementTree as ET
from nltk.tokenize import WordPunctTokenizer as wpt
from nltk.tokenize import WhitespaceTokenizer as wst
from nltk.tokenize import RegexpTokenizer
import re
from collections import Counter
#from lxml import etree

In [2]:
def get_paths(rootdir):
    # fetches a list of absolute paths, given a dir with xml files
    # BEHÖVS FÖR OPEN_XMLS
    file_paths = []

    for folder, _, files in os.walk(rootdir):
        for filename in files:
            if filename.endswith('xml'):
                file_paths.append(os.path.abspath(os.path.join(folder, filename)))
    return file_paths

In [4]:
allFiles = get_paths("DDICorpus/Train")
allFiles.extend(get_paths("DDICorpus/Test")) # ska vi ha båda testmapparna???


In [10]:
s = "string. With. Punctuation? don't 'hell0o cat's' micro-organisms 'chat'"

In [6]:
def string_to_span(s):
    # creates a tokenized version and a span version of a string
    # BEHÖVS FÖR OPEN_XMLS
    #s = (re.sub(r"[^A-Za-z\s]",'',s)).lower() # removes all non-alphanumerical characters LOL gör inte det
    tokenizer = RegexpTokenizer("[\w'-]+|[^\w\s]+") # tokenizes words and punctuation except hyphens in compound words and apostrophes
    tokenized = tokenizer.tokenize(s.lower())
    span = list(tokenizer.span_tokenize(s)) # gets the pythonic span i e (start, stop_but_not_including)
    new_span = []
    for tpl in span:
        new_span.append((tpl[0], (tpl[1]-1))) # to get non-pythonic span i e (start,last_char)
    return new_span, tokenized

In [7]:
def open_xmls(fileList):
    
    vocab = []
    data_df_list = [] 
    ner_df_list = []
    ent_types = []
    all_words = []
    for file in fileList:
        print("   -------------- this is one file ---------------------")
        print(f"filename: {file}")
        tree = ET.parse(file)
        root = tree.getroot()
        #tag = root.tag
        for sentence in root:
            print("--------------------- this is one sentence ---------------------")
            print(f"filename is still: {file}")
            sent_id = sentence.attrib['id']
            sent_txt= sentence.attrib['text']
            
            print("sentence id :", sent_id)
            #print("sentence text:", sent_txt)
            #split = sent_txt.split(' ') # do i need this?
            char_ids, tokenized = string_to_span(sent_txt)
            print(f'TOKENIZED {tokenized}')
            #print(f"char ids: {char_ids}")
            #print(f"tokenized: {tokenized}")
            #all_words.extend(tokenized)
            unique_w = list(set(tokenized))
            vocab.extend(unique_w)
            for i, word in enumerate(tokenized): # make this into a funciton?
                # make a tuple for each word so that the data_df is of the right height 
                # containing sentence id, actual word since token_id isn't available yet, char_start_id, char_end_id
                if 'test' in file.lower():
                    split = 'test'
                else:
                    split = 'train/dev'
                word_tpl = (sent_id, word, char_ids[i][0], char_ids[i][1], split)# one row in data_df 
                
                data_df_list.append(word_tpl)
            for entity in sentence:
                if entity.tag == 'entity':
                    ent_txt = (entity.attrib['text']).lower()
                    ent_type = (entity.attrib['type']).lower()
                    char_offset = entity.attrib['charOffset']
                    
                    if len((ent_txt.split(' '))) >= 2:
                        print("THIS FILE HAS MORE THAN ONE WORD BUT ONLY ONE CHAR SPAN:", file)
                        
                    print("CHAR OFFSET:", char_offset)
                    #char_span = entity.attrib['charOffset'].split('-')
                    char_span = (re.sub(r"[^0-9]+",' ', char_offset)).split(' ')
                    print("char offset: ", char_span)
                    print("entity text ie the actual word:", ent_txt)
                    if len(char_span) > 2:
                        
                        char_pairs = (list(zip(char_span[::2], char_span[1::2])))
                        
                        for pair in char_pairs:
                            print("INSIDE NEW LOOP BBY")
                            entity_tpl = (sent_id, ent_type, pair[0], pair[1])
                            print(entity_tpl)
                            ner_df_list.append(entity_tpl)
                    #    print(char_span)
                    #    ent_start_id, ent_end_id, ent_start_two, ent_end_two = char_span # verboten bc sometimes len(char_span) will be 4
                    #    
                    #    ent_txt = ent_txt.split(' ')
                    #    if len(ent_txt) > 2:     
                    #        if (int(ent_end_id) - int(ent_start_id)) > (int(ent_end_two) - int(ent_start_two)):
                    #            print("hello")
                    #            
                    #    #entity_tpl_two = (sent_id, ent_type, ent_start_two, ent_end_two)
                    #    #ner_df_list.append(entity_tpl_two)
                    #elif len(char_span) == 6:
                    #    print(char_span)
                    #    
                    #    #print("2nd entity: ", ent_txt_two, sent_id, ent_type, ent_start_two, ent_end_two)
                    else:
                        print(char_span)
                        ent_start_id, ent_end_id = char_span
                        ent_txt_one = ent_txt
                        print("type: ", ent_type)
                    
                    
                    #print("entity charOffset ie start and end", ent_start_id)
                    #print("entity charOffset ie start and end", ent_end_id)
                #write csv line with all this info and ie sentence id, char start & end
                # also simultaneously gather words for vocab : ) then 
                        print("NO LOOP IE WHEN LEN(CHAR_SPAN) = 2: ", sent_id, ent_type, ent_start_id, ent_end_id)
                        
                        
                        ent_types.append(ent_type)
                        entity_tpl = (sent_id, ent_type, ent_start_id, ent_end_id) # ent_start_id, ent_end_id
                        
                        ner_df_list.append(entity_tpl)
                    
    
    vocab = list(sorted(set(vocab)))
    return vocab, data_df_list, ner_df_list, ent_types, all_words

In [115]:
vocab, data_df_list, ner_df_list, entities, all_words = open_xmls(allFiles)

   -------------- this is one file ---------------------
filename: /home/gushansad@GU.GU.SE/lt2316-ml/a1/DDICorpus/Train/MedLine/3881461.xml
--------------------- this is one sentence ---------------------
filename is still: /home/gushansad@GU.GU.SE/lt2316-ml/a1/DDICorpus/Train/MedLine/3881461.xml
sentence id : DDI-MedLine.d12.s0
TOKENIZED ['dexamethasone', 'and', 'retinyl', 'acetate', 'similarly', 'inhibit', 'and', 'stimulate', 'egf-', 'or', 'insulin-induced', 'proliferation', 'of', 'prostatic', 'epithelium', '.']
CHAR OFFSET: 0-12
char offset:  ['0', '12']
entity text ie the actual word: dexamethasone
['0', '12']
type:  drug
NO LOOP IE WHEN LEN(CHAR_SPAN) = 2:  DDI-MedLine.d12.s0 drug 0 12
THIS FILE HAS MORE THAN ONE WORD BUT ONLY ONE CHAR SPAN: /home/gushansad@GU.GU.SE/lt2316-ml/a1/DDICorpus/Train/MedLine/3881461.xml
CHAR OFFSET: 18-32
char offset:  ['18', '32']
entity text ie the actual word: retinyl acetate
['18', '32']
type:  drug
NO LOOP IE WHEN LEN(CHAR_SPAN) = 2:  DDI-MedLine.

entity text ie the actual word: nnrti
['118', '122']
type:  group
NO LOOP IE WHEN LEN(CHAR_SPAN) = 2:  DDI-MedLine.d132.s9 group 118 122
--------------------- this is one sentence ---------------------
filename is still: /home/gushansad@GU.GU.SE/lt2316-ml/a1/DDICorpus/Train/MedLine/11217868.xml
sentence id : DDI-MedLine.d132.s10
TOKENIZED ['efavirenz', 'has', 'demonstrated', 'superiority', 'over', 'nelfinavir', 'in', 'nucleoside-experienced', 'patients', ',', 'although', 'combining', 'these', '2', 'agents', 'may', 'represent', 'the', 'best', 'approach', 'in', 'these', 'circumstances', '.']
CHAR OFFSET: 0-8
char offset:  ['0', '8']
entity text ie the actual word: efavirenz
['0', '8']
type:  drug
NO LOOP IE WHEN LEN(CHAR_SPAN) = 2:  DDI-MedLine.d132.s10 drug 0 8
CHAR OFFSET: 44-53
char offset:  ['44', '53']
entity text ie the actual word: nelfinavir
['44', '53']
type:  drug
NO LOOP IE WHEN LEN(CHAR_SPAN) = 2:  DDI-MedLine.d132.s10 drug 44 53
--------------------- this is one sentence ---

TOKENIZED ['reduced', 'levels', '(', 'up', 'to', '20', '%)', 'of', 'total', 'glutathione', '(', 'total', 'gsh', '),', 'and', 'elevation', 'of', 'conjugated', 'dienes', '(', 'approximately', '60', '%', 'in', 'liver', 'by', 'single', 'dose', 'at', '4', 'h', ')', 'also', 'indicated', 'the', 'presence', 'of', 'an', 'oxidative', 'insult', '.']
--------------------- this is one sentence ---------------------
filename is still: /home/gushansad@GU.GU.SE/lt2316-ml/a1/DDICorpus/Train/MedLine/11137320.xml
sentence id : DDI-MedLine.d126.s5
TOKENIZED ['glutathione-s-transferase', '(', 'gst', ')', 'activity', ',', 'however', ',', 'did', 'not', 'differ', 'from', 'control', 'values', 'for', 'any', 'dose', 'or', 'at', 'any', 'time', 'point', 'in', 'cerebral', 'and', 'hepatic', 'tissues', '.']
--------------------- this is one sentence ---------------------
filename is still: /home/gushansad@GU.GU.SE/lt2316-ml/a1/DDICorpus/Train/MedLine/11137320.xml
sentence id : DDI-MedLine.d126.s6
TOKENIZED ['pretreat

TOKENIZED ['current', 'immunosuppressive', 'therapies', 'are', 'effective', 'but', 'can', 'be', 'associated', 'with', 'significant', 'adverse', 'reactions', '.']
--------------------- this is one sentence ---------------------
filename is still: /home/gushansad@GU.GU.SE/lt2316-ml/a1/DDICorpus/Train/MedLine/16649344.xml
sentence id : DDI-MedLine.d118.s2
TOKENIZED ['sirolimus', 'works', 'differently', 'from', 'the', 'immunosuppressants', 'currently', 'available', ',', 'and', 'except', 'for', 'increased', 'lipid', 'levels', ',', 'the', 'adverse', 'reaction', 'profile', 'of', 'sirolimus', 'does', 'not', 'appear', 'to', 'overlap', 'to', 'any', 'great', 'extent', 'with', 'that', 'associated', 'with', 'cyclosporine', 'or', 'tacrolimus', '.']
CHAR OFFSET: 0-8
char offset:  ['0', '8']
entity text ie the actual word: sirolimus
['0', '8']
type:  drug
NO LOOP IE WHEN LEN(CHAR_SPAN) = 2:  DDI-MedLine.d118.s2 drug 0 8
CHAR OFFSET: 37-54
char offset:  ['37', '54']
entity text ie the actual word: immu

TOKENIZED ['these', 'results', ',', 'together', 'with', 'the', 'known', 'relationships', 'between', 'estrogen', 'and', 'the', 'immune', 'response', ',', 'suggest', 'that', 'estrogens', 'affect', 'the', 'course', 'of', 'septic', 'shock', 'in', 'a', 'complex', 'fashion', 'and', 'may', 'have', 'either', 'protective', 'or', 'deleterious', 'effect', '.']
CHAR OFFSET: 61-68
char offset:  ['61', '68']
entity text ie the actual word: estrogen
['61', '68']
type:  group
NO LOOP IE WHEN LEN(CHAR_SPAN) = 2:  DDI-MedLine.d39.s8 group 61 68
CHAR OFFSET: 108-116
char offset:  ['108', '116']
entity text ie the actual word: estrogens
['108', '116']
type:  group
NO LOOP IE WHEN LEN(CHAR_SPAN) = 2:  DDI-MedLine.d39.s8 group 108 116
   -------------- this is one file ---------------------
filename: /home/gushansad@GU.GU.SE/lt2316-ml/a1/DDICorpus/Train/MedLine/1115445.xml
--------------------- this is one sentence ---------------------
filename is still: /home/gushansad@GU.GU.SE/lt2316-ml/a1/DDICorpus/Trai

...

type:  drug
NO LOOP IE WHEN LEN(CHAR_SPAN) = 2:  DDI-DrugBank.d413.s14 drug 111 121
--------------------- this is one sentence ---------------------
filename is still: /home/gushansad@GU.GU.SE/lt2316-ml/a1/DDICorpus/Train/DrugBank/Allopurinol_ddi.xml
sentence id : DDI-DrugBank.d413.s15
TOKENIZED ['although', 'a', 'causal', 'mechanism', 'and', 'a', 'cause-and-effect', 'relationship', 'have', 'not', 'been', 'established', ',', 'current', 'evidence', 'suggests', 'that', 'renal', 'function', 'should', 'be', 'monitored', 'in', 'patients', 'on', 'thiazide', 'diuretics', 'and', 'allopurinol', 'even', 'in', 'the', 'absence', 'of', 'renal', 'failure', ',', 'and', 'dosage', 'levels', 'should', 'be', 'even', 'more', 'conservatively', 'adjusted', 'in', 'those', 'patients', 'on', 'such', 'combined', 'therapy', 'if', 'diminished', 'renal', 'function', 'is', 'detected', '..']
THIS FILE HAS MORE THAN ONE WORD BUT ONLY ONE CHAR SPAN: /home/gushansad@GU.GU.SE/lt2316-ml/a1/DDICorpus/Train/DrugBank/Allopu

char offset:  ['206', '214']
entity text ie the actual word: isoniazid
['206', '214']
type:  drug
NO LOOP IE WHEN LEN(CHAR_SPAN) = 2:  DDI-DrugBank.d313.s2 drug 206 214
THIS FILE HAS MORE THAN ONE WORD BUT ONLY ONE CHAR SPAN: /home/gushansad@GU.GU.SE/lt2316-ml/a1/DDICorpus/Train/DrugBank/Insulin recombinant_ddi.xml
CHAR OFFSET: 217-241
char offset:  ['217', '241']
entity text ie the actual word: phenothiazine derivatives
['217', '241']
type:  group
NO LOOP IE WHEN LEN(CHAR_SPAN) = 2:  DDI-DrugBank.d313.s2 group 217 241
CHAR OFFSET: 244-253
char offset:  ['244', '253']
entity text ie the actual word: somatropin
['244', '253']
type:  drug
NO LOOP IE WHEN LEN(CHAR_SPAN) = 2:  DDI-DrugBank.d313.s2 drug 244 253
THIS FILE HAS MORE THAN ONE WORD BUT ONLY ONE CHAR SPAN: /home/gushansad@GU.GU.SE/lt2316-ml/a1/DDICorpus/Train/DrugBank/Insulin recombinant_ddi.xml
CHAR OFFSET: 256-271
char offset:  ['256', '271']
entity text ie the actual word: thyroid hormones
['256', '271']
type:  group
NO LOOP I

type:  group
NO LOOP IE WHEN LEN(CHAR_SPAN) = 2:  DDI-DrugBank.d248.s0 group 234 248
   -------------- this is one file ---------------------
filename: /home/gushansad@GU.GU.SE/lt2316-ml/a1/DDICorpus/Train/DrugBank/Ertapenem_ddi.xml
--------------------- this is one sentence ---------------------
filename is still: /home/gushansad@GU.GU.SE/lt2316-ml/a1/DDICorpus/Train/DrugBank/Ertapenem_ddi.xml
sentence id : DDI-DrugBank.d329.s0
TOKENIZED ['when', 'ertapenem', 'is', 'co-administered', 'with', 'probenecid', '(', '500', 'mg', 'p', '.', 'o', '.', 'every', '6', 'hours', '),', 'probenecid', 'competes', 'for', 'active', 'tubular', 'secretion', 'and', 'reduces', 'the', 'renal', 'clearance', 'of', 'ertapenem', '.']
CHAR OFFSET: 5-13
char offset:  ['5', '13']
entity text ie the actual word: ertapenem
['5', '13']
type:  drug
NO LOOP IE WHEN LEN(CHAR_SPAN) = 2:  DDI-DrugBank.d329.s0 drug 5 13
CHAR OFFSET: 39-48
char offset:  ['39', '48']
entity text ie the actual word: probenecid
['39', '48']
typ

NO LOOP IE WHEN LEN(CHAR_SPAN) = 2:  DDI-DrugBank.d47.s0 drug 120 127
CHAR OFFSET: 132-140
char offset:  ['132', '140']
entity text ie the actual word: carbidopa
['132', '140']
type:  drug
NO LOOP IE WHEN LEN(CHAR_SPAN) = 2:  DDI-DrugBank.d47.s0 drug 132 140
CHAR OFFSET: 142-149
char offset:  ['142', '149']
entity text ie the actual word: levodopa
['142', '149']
type:  drug
NO LOOP IE WHEN LEN(CHAR_SPAN) = 2:  DDI-DrugBank.d47.s0 drug 142 149
--------------------- this is one sentence ---------------------
filename is still: /home/gushansad@GU.GU.SE/lt2316-ml/a1/DDICorpus/Train/DrugBank/Carbidopa_ddi.xml
sentence id : DDI-DrugBank.d47.s1
TOKENIZED ['for', 'patients', 'receiving', 'monoamine', 'oxidase', 'inhibitors', ',', 'see', 'contraindications', '.']
THIS FILE HAS MORE THAN ONE WORD BUT ONLY ONE CHAR SPAN: /home/gushansad@GU.GU.SE/lt2316-ml/a1/DDICorpus/Train/DrugBank/Carbidopa_ddi.xml
CHAR OFFSET: 23-50
char offset:  ['23', '50']
entity text ie the actual word: monoamine oxidase i

sentence id : DDI-DrugBank.d491.s17
TOKENIZED ['reproductive', 'toxicology', 'studies', 'have', 'been', 'performed', 'in', 'cynomolgus', 'monkeys', 'at', 'doses', 'up', 'to', '5', 'mg', '/', 'kg', '/', 'week', '(', 'about', '62', 'times', 'the', 'human', 'dose', 'based', 'on', 'body', 'weight', ')', 'and', 'have', 'revealed', 'no', 'evidence', 'of', 'impaired', 'fertility', 'or', 'harm', 'to', 'the', 'fetus', 'due', 'to', 'amevive', '.']
CHAR OFFSET: 235-241
char offset:  ['235', '241']
entity text ie the actual word: amevive
['235', '241']
type:  brand
NO LOOP IE WHEN LEN(CHAR_SPAN) = 2:  DDI-DrugBank.d491.s17 brand 235 241
--------------------- this is one sentence ---------------------
filename is still: /home/gushansad@GU.GU.SE/lt2316-ml/a1/DDICorpus/Train/DrugBank/Alefacept_ddi.xml
sentence id : DDI-DrugBank.d491.s18
TOKENIZED ['no', 'abortifacient', 'or', 'teratogenic', 'effects', 'were', 'observed', 'in', 'cynomolgus', 'monkeys', 'following', 'intravenous', 'bolus', 'injections'

In [91]:
data_df = pd.DataFrame(data_df_list, columns=['sent id', 'token', 'char start id', 'char end id', 'split'])

In [109]:
ner_df = pd.DataFrame(ner_df_list, columns=['sent id', 'ent_type', 'ent_start_id', 'ent_end_id'])

In [100]:
count = Counter(list(data_df['token']))

In [107]:
{w:i for w, i in count.items() if int(i) <= 10 and if w not in }

{'retinyl': 6,
 'stimulate': 1,
 'egf-': 1,
 'insulin-induced': 2,
 'proliferation': 7,
 'prostatic': 4,
 'epithelium': 4,
 'proliferates': 1,
 'defined': 3,
 'medium': 7,
 'consisting': 2,
 'basal': 7,
 'rpmi1640': 2,
 'transferrin': 2,
 'microgram': 2,
 'egf': 5,
 'iu': 2,
 'modify': 7,
 'mitogenic': 2,
 'stimulated': 6,
 'glucocorticoids': 9,
 'retinoids': 4,
 'regulate': 2,
 'prostate': 2,
 'modification': 7,
 'designs': 4,
 'joint': 6,
 'logistic': 2,
 'regression': 4,
 'models': 8,
 'interest': 3,
 'lies': 2,
 'enhancing': 8,
 'efficacious': 2,
 'limiting': 2,
 'statistical': 3,
 'work': 3,
 'focused': 2,
 'developing': 7,
 'mathematical': 1,
 'functions': 5,
 'dose-response': 3,
 'curves': 5,
 'relatively': 5,
 'regard': 5,
 'designing': 2,
 'assessing': 1,
 'parametric': 1,
 'probability': 1,
 'typically': 1,
 'nonlinear': 4,
 'weighted': 1,
 'squares': 1,
 'approach': 6,
 'purpose': 3,
 'applicable': 3,
 'across': 4,
 'wide': 4,
 'settings': 1,
 'continuous': 4,
 'discrete': 1

In [ ]:
(count['drug'] + count['drug_n'] + count['group'] + count['brand']) /(len(all_words)) # obalans

In [99]:
data_df[data_df['token'] != '']

sent id          token  char start id  char end id  \
0         DDI-MedLine.d12.s0  dexamethasone              0           12   
1         DDI-MedLine.d12.s0            and             14           16   
2         DDI-MedLine.d12.s0        retinyl             18           24   
3         DDI-MedLine.d12.s0        acetate             26           32   
4         DDI-MedLine.d12.s0      similarly             34           42   
...                      ...            ...            ...          ...   
150318  DDI-DrugBank.d566.s5          avoid            227          231   
150319  DDI-DrugBank.d566.s5       impeding            233          240   
150320  DDI-DrugBank.d566.s5          their            242          246   
150321  DDI-DrugBank.d566.s5     absorption            248          257   
150322  DDI-DrugBank.d566.s5              .            258          258   

            split  
0       train/dev  
1       train/dev  
2       train/dev  
3       train/dev  
4       train/dev  
...           ...  
150318  train/dev  
150319  train/dev  
150320  train/dev  
150321  train/dev  
150322  train/dev  

[150323 rows x 5 columns]

In [82]:
# tar hela vocabet från open_xmls
def word2int(vocabList):
    #w2i = {} # dictionary mapping words to integers
    #for i, w in enumerate(sorted((vocabList))):
    #    w2i[w] = i # because we want to be able to get integers by giving word as a key
    #return w2i
    
    return {w:i for i,w in enumerate(sorted(vocabList))} # FASTER
w2i = word2int(vocab)

In [83]:
w2i

{'"': 0,
 '",': 1,
 '";': 2,
 '">': 3,
 '#': 4,
 '%': 5,
 '%)': 6,
 '%),': 7,
 '%).': 8,
 '%);': 9,
 '%,': 10,
 '%-': 11,
 '%.': 12,
 '%;': 13,
 '&': 14,
 "''": 15,
 "''cidal": 16,
 "''static''": 17,
 "'applicability'": 18,
 "'clarity": 19,
 "'cold'": 20,
 "'consider'": 21,
 "'regularly'": 22,
 "'s": 23,
 "'tools": 24,
 '(': 25,
 '(&': 26,
 "('": 27,
 '(+)': 28,
 '(+)-': 29,
 '(+/-': 30,
 '(+/-)': 31,
 '(-': 32,
 '(-)': 33,
 '(-)-': 34,
 '(-/-)': 35,
 '(<': 36,
 '(=': 37,
 '(>': 38,
 '([': 39,
 '(~': 40,
 ')': 41,
 ')%': 42,
 '))': 43,
 ')),': 44,
 '))-': 45,
 ')).': 46,
 ')*': 47,
 '),': 48,
 ')-': 49,
 ')-,': 50,
 ')--': 51,
 ').': 52,
 ')..': 53,
 ')/': 54,
 '):': 55,
 ');': 56,
 ')=': 57,
 ')]': 58,
 ')].': 59,
 '*': 60,
 '**': 61,
 '**)': 62,
 '**,': 63,
 '*,': 64,
 '*;': 65,
 '+': 66,
 '+)': 67,
 '+)-': 68,
 '+)](': 69,
 '+-': 70,
 '+/-': 71,
 ',': 72,
 ',)': 73,
 '-': 74,
 '--': 75,
 '--------------------------------------------------------------------------------': 76,
 '-0': 7

In [ ]:
# efter data_df_list är en dataframe och efter vocab har blivit w2i
# tar data_df-kolumnen för tokens
def get_token_ids(tokensList, vocab2idDict):
    # fetches token id from vocab2id dict
    #token_ids = []
    #for w in tokensList:
    #    print(w)
    #    token_ids.append(vocab2idDict[w])
    #return token_ids
    return [vocab2idDict[w] for w in tokensList] # SNABBARE


In [74]:
import time
start = time.time()
tokenizer = RegexpTokenizer("[0-9]+")
tokenizer.tokenize(nums)
end = time.time()
print(end - start)

0.00025153160095214844


In [ ]:
pddf['token id'] = token_ids

In [ ]:
pddf.drop(columns=['token'])

In [ ]:
vocab2idd['the']

In [73]:
0.00021696090698242188


0.00021696090698242188

In [ ]:
sus = "Drug interaction studies with SUSTIVA and these imidazole and triazole antifungals have not been conducted."

In [ ]:
a = ['cat', 'dog', 'hamster', 'monkey', 'banana']
b = ['cat', 'hamster', 'apple', 'pear', 'banana']

In [ ]:
set(a) ^ set(b)

In [ ]:
import timeit
init = "a = ['cat', 'dog', 'hamster', 'monkey', 'banana']; b = ['cat', 'hamster', 'apple', 'pear', 'banana']"
print(timeit.timeit('list(set(a) - set(b))', init, number = 100000))
print(timeit.timeit('s = set(b);[x for x in a if x not in s]', init, number = 100000))
print(timeit.timeit('set(a) ^ set(b)', init, number = 100000))
print(timeit.timeit('[item for item in a if item not in b]', init, number = 100000))

In [ ]:
import csv
with open('eggs.csv', 'w', newline='') as csvfile:
    spamwriter = csv.writer(csvfile, delimiter=' ',
                            quotechar='|', quoting=csv.QUOTE_MINIMAL)
    spamwriter.writerow(['Spam'] * 5 + ['Baked Beans'])
    spamwriter.writerow(['Spam', 'Lovely Spam', 'Wonderful Spam'])

In [2]:
abc = "string With. Punctuation: don't HElL0 c4T5."

In [70]:
s = (re.sub(r"[^0-9]+",' ',nums)).split(' ')

In [71]:
s

['11', '5123', '502', '112', '838', '999']

In [71]:
kates = "I shouldn\'t really but, okay I will. I love 'Rocky' and calcium-rich foods -- bananas for example."

In [68]:
k = (re.sub(r"\w+|[^\w\s]+",' ',kates)).lower()

In [61]:
tokenizer = RegexpTokenizer("[0-9]+")
tokenizer.tokenize(nums)

In [58]:
nums = "11-5123;502-112;838-999"

In [59]:
tokenizer = RegexpTokenizer("[\w'-]+|[^\w\s]+")

In [77]:
tok = tokenizer.tokenize(nums)

In [9]:
tok1 = ['85', '92', '103', '111', '146', '153']

In [34]:
toktok = "thiazide diuretics paraply"

In [92]:
idx = int(tok1[1]) - int(tok1[0])

In [35]:
len(toktok)

26

In [36]:
for item in lol:
    print(int(item[1])- int(item[0]))

7
8
7


In [37]:
len_w = [int(tpl[1])-int(tpl[0]) for tpl in lol]

In [65]:
ltoktok = list(toktok)
def get_word_span(charOffsetList, entTxt, sentId, entType):
    
    ners = []
    span_pairs = list(zip(charOffsetList[::2], charOffsetList[1::2]))
    ent_txt = list(entTxt)
    w_len = [int(tpl[1])-int(tpl[0]) for tpl in span_pairs] # len of each word in entity
    
    for i, n in enumerate(w_len):

        ners.append((''.join((ent_txt[:n+1])), span_pairs[i][0], span_pairs[i][1]))
        #print(lol[i])
        #print(ltoktok)
        del ent_txt[:n+2]
    return ners

In [67]:
a = get_word_span(tok1, toktok)

In [69]:
a.extend(get_word_span(tok1, toktok))

In [70]:
a

[('thiazide', '85', '92'),
 ('diuretics', '103', '111'),
 ('paraply', '146', '153'),
 ('thiazide', '85', '92'),
 ('diuretics', '103', '111'),
 ('paraply', '146', '153')]

In [60]:
lol = list(zip(tok1[::2], tok1[1::2]))

In [61]:
lol

[('85', '92'), ('103', '111'), ('146', '153')]

In [81]:
tokenizer.tokenize(kates)

['I',
 "shouldn't",
 'really',
 'but',
 ',',
 'okay',
 'I',
 'will',
 '.',
 'I',
 'love',
 "'Rocky'",
 'and',
 'calcium-rich',
 'foods',
 '--',
 'bananas',
 'for',
 'example',
 '.']

In [ ]:
zxc = string_to_span(s)

In [ ]:
dfObj = pd.DataFrame(zxc)

In [ ]:
dfObj

In [ ]:
z = "The concurrent use of Robinul Injection with other anticholinergics or medications with anticholinergic activity, such as phenothiazines, antiparkinson drugs, or tricyclic antidepressants, may intensify the antimuscarinic effects and may result in an increase in anticholinergic side effects."

In [ ]:
for i, x in enumerate(z): 
    print(i, x)

In [ ]:
# YOU DON'T NEED THIS 
# list(spans_to_relative(wst().span_tokenize(s))) # how long the words are

In [35]:
import string

account_number = input("Enter the account number to which you want to transfer money: ")
value = input("Enter the amount you would like to transfer: ")

final_account_number = account_number.translate(str.maketrans('', '', string.punctuation)
)
final_value = value.translate(str.maketrans('', '', string.punctuation)
)

print(final_account_number)
print(final_value)

Enter the account number to which you want to transfer money: a
Enter the amount you would like to transfer: a
a
a


In [40]:
string.punctuation

'!"#$%&\'()*+,-./:;<=>?@[\\]^_`{|}~'

In [37]:
stringy = "'string. With. Punctuation? don't 'hell0o cat's' micro-organisms 'chat'"

In [63]:
zup, xup = string_to_span(s)

In [65]:
[x for x in xup if len(regex.findall(x)) > 1 or len(regex.findall(x)) == 0]

['string',
 '.',
 'with',
 '.',
 'punctuation',
 "cat's'",
 'micro-organisms',
 "'chat'"]

In [73]:
regex = re.compile("[@_!#$%^&*()<>?/\|}{~:\']+") 

In [48]:
regex.findall(stringy)

["'", '?', "'", "'", "'", "'", "'", "'"]

In [57]:
wpt().tokenize(stringy)

["'",
 'string',
 '.',
 'With',
 '.',
 'Punctuation',
 '?',
 'don',
 "'",
 't',
 "'",
 'hell0o',
 'cat',
 "'",
 's',
 "'",
 'micro',
 '-',
 'organisms',
 "'",
 'chat',
 "'"]